# Fonctions d'une variable complexe (I)

Marc Lorenzi

7 avril 2019

In [ ]:
import matplotlib.pyplot as plt
import cmath
import math
import colorsys
import random

In [ ]:
plt.rcParams['figure.figsize'] = (10, 10)

Nous allons explorer "visuellement" quelques fonctions $\mathbb C\to \mathbb C$. Après une petite discussion sur le modèle de couleurs HSV, nous verrons une méthode pour représenter les fonctions de variable complexe. But totalement avoué de ce notebook : mettre en évidence graphiquement quelques propriétés remarquables d'une classe particulière de fonctions de la variable complexe : les fonctions __holomorphes__.

## 1. représenter graphiquement une fonction d'une variable complexe

### 1.1 Le modèle de couleurs HSV

Le modèle __HSV (Hue, Separation, Value)__ est un modèle de couleurs plus intuitif à manipuler que le modèle standard RGB (Red, Green, Blue). Chaque couleur est représentée par un triplet $(h, s, v)$ où

- $h$ ("hue", "teinte" en français) est la couleur au sens "naïf". $h=0$ correspond au rouge. Lorsque $h$ augmente, on passe par les couleurs de l'arc en ciel : rouge, orange, jaune, vert, bleu, violet ... puis, lorsque $h$ tend vers 1, on passe du violet au rouge. Nous avons donc un cycle de couleurs.

- $s$ est la saturation. plus $s$ est petit, plus les couleurs sont "fades" (pour $s=0$ on obtient les niveaux de gris). Dans le système RGB, augmenter $s$ consiste à augmenter le minimum des trois valeurs $r,g,b$.

- $v$ ("value", "brightness", "luminance" ou "brillance" en français) est la brillance de la couleur. Dans le système RGB, augmenter $v$ consiste à augmenter simultanément $r,g,b$ en gardant leurs proportions respectives constantes.

Ci-dessous, le disque de centre $O$ et de rayon 1. Pour tout nombre complexe $z=re^{i\theta}$ où $0\le r\le 1$ et $0\le \theta\le2\pi$ on colorie le point correspondant en prenant $(h,s,v)=(\frac{\theta}{2\pi},1, r)$. La fonction `cmath.phase` renvoyant un argument de $z$ dans l'intervalle $]-\pi,\pi]$, on adapte évidemment la valeur de $\theta$. 

In [ ]:
N = 400
m = [[(0, 0, 0) for i in range(N)] for j in range(N)]
for i in range(N):
    for j in range(N):
        x = -1.2 + j * 2.4 / N
        y = 1.2 - i * 2.4 / N
        z = x + 1j * y
        theta = cmath.phase(z)
        if theta < 0: theta = theta + 2 * math.pi
        r = abs(z)
        if r <= 1: m[i][j] = colorsys.hsv_to_rgb(theta / (2 * math.pi), 1, r)
plt.imshow(m, extent=[-1.2, 1.2, -1.2, 1.1])

Remarquez comment

- Les couleurs deviennent plus brillantes du centre vers le brod du disque.
- Lorsqu'on tourne autour de l'origine, les couleurs décrivent les couleurs de l'arc en ciel.

Nous allons maintenant utiliser le modèle HSV pour dessiner des fonctions $\mathbb C\to\mathbb C$. Et expliquer comment se comportent ces fonctions.

### 1.2 Introduction

Comment dessiner une fonction $f:\mathbb C\to\mathbb C$ ? Évidemment, l'idéal serait que mes lecteurs puissent voir dans un espace de dimension 4. Mais comme il est possible que ce ne soit pas le cas pour tous, nous allons procéder autrement. Diverses méthodes existent, nous allons nous concentrer sur l'une d'entre-elles. Pour tout $z\in\mathbb C$, nous colorions le point du plan d'affixe $z$ avec une couleur qui dépend de $f(z)$. Comme $f(z)$ est essentiellement un objet bidimensionnel, nous utiliserons des couleurs qui dépendent de deux paramètres.

À partir d'ici, des choix stratégiques s'imposent. Rien ne vous empêche bien entendu d'essayer d'autres possibilités. Nous allons colorier le point d'affixe $z$ avec la couleur $(h, s, v)$ (dans le modèle HSV, donc) où 

$$h=\arg f(z),s=1,v=|f(z)|$$

Enfin, c'est à peu près cela. Car, rappelons-nous, les paramètres $h,s,v$ doivent appartenir à $[0,1]$. Pour $h$, c'est facile. La fonction `cmath.phase` renvoie l'argument du nombre complexe $z$, entre $-\pi$ et $\pi$. Ramener la valeur à l'intervalle $[0,1]$ se fait aisément.

In [ ]:
def arg01(z):
    theta = cmath.phase(z) / (2 * math.pi)
    if theta < 0: return theta + 1
    else: return theta

In [ ]:
for z in [4, 1j, -1j, 1+1j, -2, 2 - 2* 1j]:
    print(z, arg01(z))

Le module de $f(z)$, en revanche, varie sur $\mathbb R_+$. J'ai choisi ici de prendre

$$v=\left|\sin\left(\frac \pi m \log_2(1 + |f(z)|)\right)\right|^d$$

où $m$ et $d$ sont deux paramètres. J'imagine que vous attendez quelques explications :-) ...

- Grâce au logarithme, lorsque le module de $f(z)$ double, la quantité augmente environ de 1
- Le sinus permet d'obtenir des variations périodiques de période $m$, où $m$ peut être choisi comme on le désire.
- L'exposant $d$ est un paramètre de "dureté". Plus $d$ est grand, plus les contrastes sont importants. La valeur $d=1$ est tout à fait acceptable dans la plupart des cas, mais on se réserve la possibilité de la modifier.

In [ ]:
def psi(x, m, d):
    if x == 0: return 0
    else:
        return abs(math.sin(math.pi * math.log(x, 2) / m)) ** d

Un petit dessin vaut mieux qu'un long discours, alors écrivons la fonction de tracé.

### 1.3 La fonction de tracé

La fonction `plot_complex` prend en paramètres :

- Une liste `extent` de 4 flottants : les abscisses minimale et maximale et les ordonnées minimale et maximale des points à tracer.
- Un paramètre $m$ dont nous avons déjà parlé.
- Un paramètre $d$ dont nous avons aussi parlé.
- deux paramètres `nx` et `ny` qui sont le nombre de lignes et de colonnes de l'image que nous voulons afficher.

In [ ]:
def plot_complex(f, extent=[-1.5, 1.5, -1.5, 1.5], m=1, d=0.2, nx=400, ny=400):
    xmin, xmax, ymin, ymax = extent
    ws = [[0 for i in range(nx)] for j in range(ny)]
    plt.hsv()
    for i in range(nx):
        for j in range(ny):
            x = xmin + j * (xmax - xmin) / nx
            y = ymax - i * (ymax - ymin) / ny
            z = x + 1j * y
            try:
                w = f(z)
                r = psi(abs(w), m, d)
                ph = arg01(w)
                ws[i][j] = colorsys.hsv_to_rgb(ph, 1, r)
            except: ws[i][j] = (0., 0., 0.)
    plt.imshow(ws, interpolation='bicubic', extent=extent, aspect='auto')
    plt.grid()

Le `try ... except` permet de ne pas se préoccuper d'éventuelles divisions par 0, ou autres calamités liées au calcul numérique. Si, en un point $z$, $f(z)$ n'est pas défini, le pixel correspondant est colorié en noir.

### 1.4 Un premier test

Commençons par le plus simple possible (hormis les fonctions constantes) : la fonction $z\mapsto z$.

In [ ]:
M = 8
plot_complex(lambda z: z, extent=[-M, M, -M, M])

Que voit-on ? 

- Des anneux concentriques, centrés à l'origine, d'épaisseurs de plus en plus grandes. En comptant les anneaux à partir du centre vous obtenez une idée de la valeur de $|f(z)|$. Rappelez-vous que d'un anneau à l'autre, le module est environ multiplié par 2.

- Les anneaux sont multicolores. Très précisément, les couleurs passent par toutes les couleurs de l'arc en ciel _dans le sens trigonométrique_. Ces couleurs vous donnent l'argument de $f(z)$.

__Exercice__ : Essayez les fonctions $z-1$, $z+i$, $3z+2$, $iz-1$, $-z$. Bien, vous avez compris que toutes les fonctions affines se ressemblent. Cercles concentriques autour de l'unique racine, coloriés dans le sens trigonométrique.

### 1.5 Un second test

Avant d'entrer dans le vif du sujet, essayons aussi $z\mapsto \overline z$.

In [ ]:
M = 8
plot_complex(lambda z: z.conjugate(), extent=[-M, M, -M, M])

C'est pareil que $z\mapsto z$, me direz-vous ? Oui, sauf que c'est le contraire ! Cette fois-ci les couleurs de l'arc en ciel sont parcourues dans le sens trigonométrique __inverse__.

__Moralité__ : Dans ce qui va suivre, regardez toujours dans quel sens varient les couleurs, c'est essentiel.

## 2. Polynômes

### 2.1 Commençons par le commencement

Quel est le polynôme le plus simple dont le degré soit au moins 2 ? $X^2$ ? Ou $X^2-1$ ? Ou ... Essayons les deux. À vous d'en tester d'autres.

In [ ]:
M = 5
plot_complex(lambda z: z ** 2, extent=[-M, M, -M, M])

Voyez-vous la racine double ??? Le cycle des couleurs est parcouru __DEUX__ fois à chaque tour autour de l'origine : imaginez un nombre complexe $z$ qui se promène sur un cercle de centre $O$. Quand $z$ a fait __UN__ tour, $z^2$ a fait __DEUX__ tours. Pourquoi ? Tout simplement parce que $\arg(z^2)=2\arg z$.

Essayons maintenant $X^2-1$.

### 2.2 Deux racines simples

In [ ]:
M = 2
plot_complex(lambda z: z ** 2 - 1, extent=[-M, M, -M, M])

Vous devriez voir les deux racines simples (un cycle de couleurs) $-1$ et $1$. Remarquez aussi les ellipses entourant les deux racines simultanément : __DEUX__ cycles de couleurs !

__Exercice__ : Mettez $M$ à 100 ci-dessus. Alors, $X^2$ et $X^2-1$ sont-ils si différents, vus de loin ?

### 2.3 Une racine double, deux racines simples

Essayons un peu plus compliqué, le polynôme $X(X^2+X+1)$.

In [ ]:
M = 1
plot_complex(lambda z: z ** 2 * (z ** 2 + z + 1), extent=[-M, M, -M, M])

__Exercice__ : Combien de cycles de couleurs sur les courbes entourant chaque racine ? Et sur les "cercles" qui entourent l'ensemble de toutes les racines ?

__Exercice__ : À vous de jouer avec vos polynômes préférés. Racines simples, racines multiples, $X^n-1$, polynômes aléatoires, il y a de quoi faire.

## 3. Fractions rationnelles

### 3.1 La fraction la plus simple

Commençons par $\frac 1 X$.

In [ ]:
M = 2
plot_complex(lambda z: 1 / z, extent=[-M, M, -M, M])

Bon, c'est comme $z\mapsto z$ ? Non, car les couleurs tournent en sens inverse. Pourquoi ? Parce que $\arg\frac 1 z=-\arg z$.

### 3.2 Pôle double

Traçons maintenant $\frac 1 {X^2}$.

In [ ]:
M = 2
plot_complex(lambda z: 1 / z ** 2, extent=[-M, M, -M, M])

Deux cycles de couleurs par tour, en sens inverse. Sans preuve :

- __Pour une racine d'ordre $n$, $n$ cycles de couleurs en sens normal__
- __Pour un pôle d'ordre $n$, $n$ cycles de couleurs en sens inverse__

### 3.3 Une fraction avec quelques pôles et racines

Pour terminer, la fraction $\frac{X^2+1}{(X-1)^2(X^2+X+1)}$.

In [ ]:
M = 3
plot_complex(lambda z: (z ** 2 + 1) / ((z - 1) ** 2 * (z ** 2 + z + 1)), extent=[-M, M, -M, M])

Deux racines simples, $-i$ et $i$. Un pôle double, $1$, et deux pôles simples, $j, j^2$. Regardez les sens de rotation, le nombre de cycles et le nombre de cercles concentriques, ils permettent de distinguer les pôles et les racines.

__Exercice__ : Mettez $M$ à 10 et $m$ à $0.05$. Se pourrait-il que ...

__Proposition : Le nombre de cycles de couleurs sur une courbe qui entoure les racines et les pôles est égal au nombre de racines moins le nombre de pôles, comptés avec leur multiplicité. C'est à dire au degré de la fraction !__

__Exercice__ : Comment reconnaît-on une fraction de degré 0 ? De degré $<0$ ? De degré $>0$ ? Expérimentez ...

## 4. Fonctions holomorphes

### 4.1 C'est quoi ?

__Définition__ : Soit $\Omega\subset\mathbb C$ un ensemble _ouvert_. Soit $f:\Omega\to\mathbb C$. On dit que $f$ est __holomorphe__ sur $\Omega$ lorsque $f$ est dérivable en tout point de $\Omega$.

Dérivable _au sens complexe_, bien entendu. C'est à dire que pour tout $z\in\Omega$, la quantité $\frac{f(z+h)-f(z)}{h}$ a une limite lorsque $h\to 0$, $h\in\mathbb C$. La définition de limite est la même que pour les fonctions de variable réelle, sauf qu'ici il est question de module et pas de valeur absolue. Et la limite de nos taux d'accroissements est évidemment appelée la dérivée de $f$ en $z$ et est notée $f'(z)$. La condition de dérivabilité au sens complexe est une condition très restructive, beaucoup plus que la dérivabilité pour les fonctions de variable réelle. Par exemple, on peut montrer qu'une fonction holomorphe est automatiquement __indéfiniment dérivable__. On peut toujours rêver d'un tel résultat pour les fonctions de variable réelle !

La théorie des fonctions holomorphes est une vaste et riche théorie, remplie de résultats très profonds.

### 4.2 Qui est holomorphe ?

Si vous ouvrez votre cours de maths sur la dérivation, vous verrez sans peine que les théorèmes sur les opérations sur les fonctions dérivables s'étendent aux fonctions $\mathbb C\to\mathbb C$ : somme, produit, quotient (là où le dénominateur ne s'annule pas), composée. Après tout, la démonstration de ces théorèmes ne repose que sur les propriétés de la valeur absolue, qui sont les mêmes que celles du module.

__Notation__ : Nous noterons $\mathcal H(\Omega)$ l'ensemble des fonctions holomorphes sur l'ouvert $\Omega$. Le paragraphe précédent nous dit que cet ensemble est stable pour l'addition, le produit des fonctions, etc.

__Proposition__ : Les fonctions constantes, les polynômes, sont holomorphes sur $\mathbb C$ et leur dérivée est formellement la même que celle obtenue pour les fonctions à valeurs réelles.

__Démonstration__ : Je passe le cas trivial des fonctions constantes. Si nous montrons que $f:z\mapsto z$ est holomorphe sur $\mathbb C$, ce sera fini, par stabilité de $\mathcal H(\mathbb C)$ par addition et multiplication. Soit donc $z\in\mathbb C$. Soit $h\in\mathbb C^*$. On a

$$\frac{f(z+h)-f(z)}{h}=\frac{(z+h)-z}{h}=1$$

Cette quantité constante tend évidemment vers 1 lorsque $h\to 0$. Ainsi $f$ est holomorphe sur $\mathbb C$ et pour tout $z\in\mathbb C$ on a $f'(z)=1$.

__Corollaire__ : Une fraction rationnelle est holomorphe sur $\mathbb C$ privé de l'ensemble des pôles de la fraction.

__Démonstration__ : C'est le quotient de deux polynômes, qui, eux, sont holomorphes.

Il existe bien d'autres fonctions holomorphes. Nous en verrons des tas d'exemples dans ce notebook.

### 4.3 Qui n'est pas holomorphe ?

Il existe des fonctions en apparence très régulières qui ne sont pas holomorphes. Voici l'exemple à ne pas manquer.

__Proposition__ : La fonction $f:z\mapsto \overline z$ n'est holomorphe sur aucun ouvert de $\mathbb C$.

__Démonstration__ : $\frac{\overline{z+h}-\overline z}{h}=\frac{\overline h}{h}$. Lorsque $h$ tend vers 0 en étant réel, cette quantité tend vers $1$. Mais si $h$ tend vers 0 en étant imaginaire pur, cette quantité tend vers $-1$. Pas de limite, donc, lorsque $h$ tend vers 0. 

__Idée en l'air__ : Les "fonctions du genre $z\mapsto f(z)=g(\overline z)$" ne sont pas holomorphes. Évidemment, tel quel cela n'a pas de sens. Par exemple $f(z)=\frac{\overline z}{\overline z}$ est holomorphe sur $\mathbb C^*$ :-). Je ne préciserai pas plus avant. 

__Proposition__ : Soit $\Omega\subset \mathbb C\to\mathbb R$ holomorphe, où $\Omega$ est un ouvert _connexe_. Alors $f$ est constante.

__Démonstration__ : Ce résultat est assez surprenant. Cela veut dire qu'une fonction holomorphe est soit triviale (constante) soit "compliquée. 

Soit $f:\Omega\subset\mathbb C\to\mathbb R$ une fonction holomorphe à valeurs réelles. Soit $z\in\Omega$. Pour $h$ réel, le quotient $\frac{f(z+h)-f(z)}{h}$ est réel. Si cette quantité a une limite lorsque $h\to 0$, alors elle doit être réelle : $f'(z)\in\mathbb R$. Mais pour $h$ imaginaire pur, le quotient $\frac{f(z+h)-f(z)}{h}$ est imaginaire pur. Si cette quantité a une limite lorsque $h\to 0$, alors elle doit être imaginaire pure : $f'(z)\in i\mathbb R$. Ainsi, $f'(z)=0$. Conclusion $f'=0$ sur $\Omega$. Nous admettrons ici que la connexité de $\Omega$ implique que $f$ est constante.

__Conséquence__ : Une fonction holomorphe ne peut pas être à valeurs uniquement réelles (à moins qu'elle ne soit constante). On peut de même montrer qu'elle ne peut pas être à valeurs uniquement imaginaires pures. Plus généralement, un théorème appelé le __théorème de l'image ouverte__ nous dit que si $f\in\mathcal H(\Omega)$ alors $f$ est ouverte, c'est à dire que l'image de tout ouvert par $f$ est encore un ouvert.

### 4.4 Qu'allons nous faire ?

Nous allons dans les deux prochains notebooks explorer des prolongements holomorphes à $\mathbb C$ (ou presque) des fonctions usuelles : exponentielle, logarithmes, racines carrées, fonctions trigonométriques. Histoire d'alléger, nous admettrons certains résultats mathématiques.